# Time Series Project

https://automotorsqueretaro.negocio.site/ https://automotorsqueretaro.negocio.site/ https://automotorsqueretaro.negocio.site/ https://automotorsqueretaro.negocio.site/

![](id_for_ideas/logo.png)

https://automotorsqueretaro.negocio.site/ https://automotorsqueretaro.negocio.site/ https://automotorsqueretaro.negocio.site/ https://automotorsqueretaro.negocio.site/

## 2.2 Etapas en el desarrollo de código



Acá se va exponiendo de forma interactiva las etapas técnicas del desarrollo de código 

# 2.2.1 DATA FEED:  Descripción del acondicionamiento del dataset original

In [4]:
import numpy as np
import pandas as pd
from paquete_proyecto.herramientas.data_info import data_info
import warnings



warnings.filterwarnings("ignore")

In [5]:
from paquete_proyecto.data_feed.bases import importar_databases, ajustes_finales
#TODO: RISE

ventas, ventas_sin_duplicados = importar_databases()

data = ajustes_finales(ventas_sin_duplicados)

## CIERRE ETAPA: 2.2.1 DATA PREPARE

### DATASET: 

#### DESCRIPCION:

- dataset original: con la variable "Fecha" como indice

In [6]:
display(data.sample(3))
display(data_info(data=data, name="ventas"))

IdCliente       NombreCliente  Empleado Referencia  \
Fecha                                                            
2016-12-20  C52530462       ERIKA MANCERA        10   VFR-0069   
2019-11-03  C19457547  MARTINEZ JOSE LUIS        50   VFR-0282   
2017-10-18  C79989871    JARAMILLO RAMIRO        36   LUA-0015   

                                Descripcion  CodigoFamilia      Familia  \
Fecha                                                                     
2016-12-20          FILTRO DE AIRE MFA-681P            109      FILTROS   
2019-11-03  FILTRO DE AIRE MFA-723/ AIP 778            109      FILTROS   
2017-10-18                  MOBIL 10W30 1/4            103  LUBRICANTES   

            Cantidad   Ventas       Localidad      Sede  Area  
Fecha                                                          
2016-12-20         1   2931.0        Engativa  Calle 80    31  
2019-11-03         1  14285.0        Engativa  Calle 80    31  
2017-10-18         1  29800.0  Barrios unidos  Av Chile    34

info de ventas        columna     type   count  NaN NaN_pct  unique unique_pct
0                   IdCliente   object  108794    0   0.0 %   24087    22.14 %
1               NombreCliente   object  108794    0   0.0 %   21816    20.05 %
2                    Empleado    int32  108794    0   0.0 %      56     0.05 %
3                  Referencia   object  108794    0   0.0 %    1854      1.7 %
4                 Descripcion   object  108794    0   0.0 %    1814     1.67 %
5               CodigoFamilia    int32  108794    0   0.0 %       5      0.0 %
6                     Familia   object  108794    0   0.0 %       5      0.0 %
7                    Cantidad    int32  108794    0   0.0 %     212     0.19 %
8                      Ventas  float64  108794    0   0.0 %   14279    13.12 %
9                   Localidad   object  108794    0   0.0 %       6     0.01 %
10                       Sede   object  108794    0   0.0 %       7     0.01 %
11                       Area    int32  108794    0   0.0 %       7     0.01 %

<div>
    <h4>Inspeccion de cada columna (DESACTUALIZADO)</h4>
    <ol>
        <li> <b>IdCliente</b>: object - código alfanumérico</li>
        <li> <b>NombreCliente</b>: object - string = Nombre, Apellido</li>
        <li> <b>>> Empleado</b>: float - cambiar a int</li>
        <li> <b>Referencia</b>: object: categoría ordinal</li>
        <li> <b>Descripcion</b>: object: categoria cualitativa </li>
        <li> <b>>> CodigoFamilia</b>: id</li>
        <li> <b>Familia</b>: Areas comerciales: son 5 que se dividen en "producto" o "servicio"</li>
        <li> <b>>>Cantidad</b>: object: cambiar a int</li>
        <li> <b>>> Ventas</b>: int: cambiar a float</li>
        <li> <b>Localidad</b>: object: categoria bussines</li>
        <li> <b>>> Area</b>: float: cambiar a int</li>
    </ol>
</div>

-----

# 2.2.2 DATA PREPARE: Tratamiento del dataset de trabajo

<b>1ro)  AÑADIR "Id"</b>

<b>2do) AJUSTE DE TIPO DE CAMBIO: "Ventas_USD"</b>

<b>3ro) CATEGORIZACION</b>

<b>4to) COMPLETAR EL DATASET CON LAS FECHAS FALTANTES</b>
    

## 1ro- AÑADIR "Id"

Añadimos un registro único para cada transacción

In [7]:
from paquete_proyecto.data_prepare.hard_code import hard_category_id

data = hard_category_id(data)

## 2do- AJUSTE DE TIPO DE CAMBIO: "Ventas_USD"

1ro) Se hace un llamado a la API de Alpha Vantage para solicitar la cotización semanal del par COP/USD<br />
2do) Se selecciona el rango de fechas pertencientes al dataset original (255 semanas)<br />
3ro) Se añade la columna "Cotizacion_USD" al dataset<br />
4to) Se añade la columna "Ventas_USD" que refleja el valor de la transacción en dolares.<br />


In [8]:
import os
from dotenv import load_dotenv

load_dotenv()

from paquete_proyecto.data_prepare.forex_api import alpha_vantage_fx_api
from paquete_proyecto.data_prepare.cotizacion import (
    criterio_valor_apertura,
    preparar_cotizacion,
    agregar_cotizacion,
)

In [9]:
TOKEN = os.environ["TOKEN_AV"]

cotizacion = alpha_vantage_fx_api("FX_WEEKLY", "COP", "USD", TOKEN)
cotizacion = criterio_valor_apertura(preparar_cotizacion(data, cotizacion), "COP/USD")

data = agregar_cotizacion(data, cotizacion)#TODO agregar el parámetro "Cotizacion_USD"
data.loc[:, "Ventas_USD"] = data["Ventas"] * data["Cotizacion_USD"]

## 3ro- CATEGORIZACION

<b>1ro) Se añade columna "category_1": Categorizacion binaria "producto", "servicio"</b><br />
    - categoria: [valores]  - servicio: [SERVICIOS, REENCAUCHE], producto: [LLANTA, FILTRO, LUBRICANTES]


<b>2do) Se añade columna "category_2": SubCategorizacion RegEx a Familia-SERVICIOS (70% de los registros):</b><br />
        - Se subcategoriza el registro "SERVICIOS" perteneciente a la variable "Familia"<br />
        - Son 14 etiquetas que surgen por extraccion de patrones RegEx desde la variable "Descripcion"<br />
        - El remamente se categorizó con la etiqueta "otros"


In [10]:
from paquete_proyecto.data_prepare.hard_code import hard_category_1

# CATEGORY_1
data = hard_category_1(data, 'category1')

In [11]:
from paquete_proyecto.data_prepare.regex import (
    return_match_id,
    category_apply,
    merge_category,
)

# CATEGORY_2
data_regex_servicios = data.loc[data["Familia"] == "SERVICIOS"].set_index("Id")


patrones = dict(
    balanceo="(BALANCEO)",
    alineacion="(ALINEACION)",
    reparacion="(REPARACION)",
    cambio_de_aceite="(CAMBIO(.?.?.?.?)ACEITE)",
    calibracion="(CALIBRACION)",
    montaje="(MONTAJE)",
    rotacion="(ROTACION)",
    mano_de_obra="(MANO(.?.?.?.?)OBRA)",
    frenos="(AJUSTE(.?.?.?.?)FRENOS|CAMBIO(.?.?.?.?)PASTILLAS|REVISION(.?.?.?.?)FRENOS)",
    rectificacion="(RECTIFICACION)",
    servicios="(SERVICIO(.?))",
    cupon_combo="(CUPON|COMBO)",
    desvare_ruta="(DESVARE(.?.?.?.?.?.?.?.?)RUTA)",
    llanta="((REGRABACION|REMANENTE|INSPECCION|MARCACION|VULCANIZADO)(.?.?.?.?.?.?.?.?.?.?.?.?.?.?.?.?)LLANTA(.?))",
    otros="Patron nulo",
)


indice_categorias = return_match_id(data_regex_servicios, "Descripcion", patrones)
feature_categoria = category_apply(data_regex_servicios, indice_categorias)

data = merge_category(data, feature_categoria, "Id", "category2")

In [12]:
# TODO: Agregar la categoría binaria "camion"
# TODO: dividir la Familia FILTROS en "aceite" y "aire"

## 4to- Completar Fecha Faltantes

In [13]:
from paquete_proyecto.data_prepare.muestreo import complete_dates

data = complete_dates(data)

## CIERRE ETAPA: 2.2.2 DATA PREPARE

### DATASET:

- Se añade "Cotizacion_USD", "Ventas_USD"," category_1", y "category_2"
- Se completan las fechas faltantes

In [14]:
display(data.sample(3))
display(data_info(data=data, name="ventas"))

Id    IdCliente                     NombreCliente  Empleado  \
Fecha                                                                        
2018-10-26  65910   C900597369            BYD MOTOR COLOMBIA SAS        44   
2017-09-11  30879   C860025900  ALPINA PRODUCTOS ALIMENTICIOS SA         2   
2017-06-04  22815  C1019006377                       LOPEZ DIEGO        22   

              Referencia                    Descripcion  CodigoFamilia  \
Fecha                                                                    
2018-10-26  SE-CS-1-0002           ALINEACION CAMIONETA            106   
2017-09-11  SE-GF-8-0004  CONTRATO DE SERVICIOS /ALPINA            106   
2017-06-04   LL-TCA-0129              SYNERIS 205/55R16            101   

              Familia  Cantidad   Ventas      Localidad            Sede  Area  \
Fecha                                                                           
2018-10-26  SERVICIOS         1    33613  Puente aranda        Calle 13    35   
2017-09-11  SERVICIOS         1  5395376         Bogota  Grandes flotas    21   
2017-06-04     LLANTA         2   386555       Engativa        Calle 80    31   

            Cotizacion_USD  Ventas_USD category1   category2  
Fecha                                                         
2018-10-26         0.00031    10.42003  servicio  alineacion  
2017-09-11         0.00034  1834.42784  servicio   servicios  
2017-06-04         0.00035   135.29425  producto         NaL

info de ventas         columna     type   count  NaN NaN_pct  unique  \
0                           Id    int32  109518    0   0.0 %  108795   
1                    IdCliente   object  109518    0   0.0 %   24088   
2                NombreCliente   object  109518    0   0.0 %   21816   
3                     Empleado    int32  109518    0   0.0 %      57   
4                   Referencia   object  109518    0   0.0 %    1855   
5                  Descripcion   object  109518    0   0.0 %    1815   
6                CodigoFamilia    int32  109518    0   0.0 %       6   
7                      Familia   object  109518    0   0.0 %       6   
8                     Cantidad    int32  109518    0   0.0 %     213   
9                       Ventas    int32  109518    0   0.0 %   14280   
10                   Localidad   object  109518    0   0.0 %       7   
11                        Sede   object  109518    0   0.0 %       8   
12                        Area    int32  109518    0   0.0 %       8   
13              Cotizacion_USD  float64  109518    0   0.0 %      14   
14                  Ventas_USD  float64  109518    0   0.0 %   23553   
15                   category1   object  109518    0   0.0 %       3   
16                   category2   object  109518    0   0.0 %      17   

info de ventas unique_pct  
0                 99.34 %  
1                 21.99 %  
2                 19.92 %  
3                  0.05 %  
4                  1.69 %  
5                  1.66 %  
6                  0.01 %  
7                  0.01 %  
8                  0.19 %  
9                 13.04 %  
10                 0.01 %  
11                 0.01 %  
12                 0.01 %  
13                 0.01 %  
14                21.51 %  
15                  0.0 %  
16                 0.02 %

-----

# (III) RESEARCH: (DESACTUALIZADO)
    1- INDICADORES CON TRATAMIENTO NUMÉRICO

    2- INDICADORES CON TRATAMIENTO CATEGÓRICO


## 1 INDICADORES TRATADOS NUMERICAMENTE

In [15]:
from paquete_proyecto.data_research.numerical import TimeSerieTarget

In [16]:
# Target 1
d1 = TimeSerieTarget(target=data["Ventas_USD"])

# Target 2
d2 = TimeSerieTarget(target=data["Cantidad"])

## 2 INDICADORES TRATADOS CATEGORICAMENTE

In [17]:
from paquete_proyecto.data_research.categorical import TimeSerieBuilder

features = [
    "Empleado",
    "Familia",
    "Localidad",
    "Sede",
    "Area",
    "category1",
    "category2"
]


features_iter = iter(features)

In [18]:
# INDICADORES TRATATOS CATEGORICAMENTE

# VOLUMEN DE VENTAS POR CATEGORIA
d3 = TimeSerieBuilder(
    dataset=data[features],
    target=data["Ventas_USD"],
)
d3.transform(lambda x: x.groupby(x.index).sum())
d3.accumulate()


# CANTIDAD DE VENTAS POR CATEGORIA
d4 = TimeSerieBuilder(
    dataset=data[features],
    target=data["Ventas_USD"],
)
d4.transform(lambda x: x.groupby(x.index).count())
d4.accumulate()

# (IV) REPORT:

indicadores solcitados:

1) Venta Total<br />
2) Ventas totales por Sedes en cada Rubro o Familia y Servicios<br />
3) Ganancia Facturación Total de Servicios<br />
4) Cantidad de Elementos vendidos<br />
5) Cantidad de Servicios Ofrecidos (CUMSUM(DUMMY))<br />
6) Ventas realizadas por sus empleados<br />
7) Cantidad de Sedes o ubicaciones disponibles<br />
8) Ranking de Ventas / Servicios de Empleados<br />

In [19]:
import plotly.express as px
from itertools import count
import os
pd.options.plotting.backend = 'plotly'

x = count()
next(x)

def crear_directorio(dir_name):
    if not dir_name.startswith("\\"):
        dir_name = "\\" + dir_name
    path = os.getcwd() + dir_name
    os.makedirs(path, exist_ok=True)
    return path

def crear_rotulo_html(prefix):
    global x
    return f"{prefix}_{next(x)}.html"

def descargar_imagen(obj, dir_name="data", prefix="img"):
    obj.write_html(crear_directorio(dir_name) +"\\"+ crear_rotulo_html(prefix=prefix))



In [20]:
# TODO: crear la funcion para crear el directorio "data" si no existe, y guardar allí los archivos html
f = d1.targets[['accum_Ventas_USD']].plot(template='plotly_dark')
f.show()
descargar_imagen(f)
f = d2.targets.Cantidad.resample('M').sum().plot(kind='bar', template='plotly_dark')#, color='red')
f.show()
descargar_imagen(f)



1) Venta Total<br />
4) Cantidad de Elementos vendidos<br />

2) Ventas totales por Sedes en cada Rubro o Familia y Servicios (iter_sum)<br />
5) Cantidad de Servicios Ofrecidos (iter_count)<br />


3) Ganancia Facturación Total de Servicios<br />
6) Ventas realizadas por sus empleados<br />
7) Cantidad de Sedes o ubicaciones disponibles<br />
8) Ranking de Ventas / Servicios de Empleados<br />

## 2. graficos del objeto TimeSerieBuilder

In [21]:
ventas_por_categoria = iter(d3.accumulated)
features_iter = iter(features)


def ordenar_columnas_por_totales(frame):
    return frame.reindex(dict(zip(frame.sum().sort_values(ascending=False).index, frame.columns)), axis=1)


def generar_contenido():
    global ventas_por_categoria
    contenido = next(ventas_por_categoria, None)
    if contenido is None:
        return
    return ordenar_columnas_por_totales(contenido)


def get_figure(content, label, suffix=None):
    if suffix is None:
        return content.plot(title=f'VISUALIZACION: Ventas por {label}', height=700, width=1200, labels={'value':'Ventas [USD]'}, template='plotly_dark')
    return content.plot(title=f'VISUALIZACION: Ventas por {label} ({suffix})', height=700, width=1200, labels={'value':'Ventas [USD]'}, template='plotly_dark')





def visualizar():
        contenido = generar_contenido()
        if contenido is None:
                return

        label = next(features_iter)
        print (label)
        f = get_figure(contenido, label)
        f.show()
        
        if input("1: guardar grafico\nENTER: pasar al siguiente"):
                descargar_imagen(f)
        return True

_visualizar = False
if _visualizar:
    while True:
            if visualizar() is None:
                    break

In [22]:
from matplotlib.pyplot import plot

class VisualizerDarkSet:
    height = 700
    width = 1200
    template = 'plotly_dark'

    def __init__(self, frame_list: list[pd.DataFrame], features: list[str], target_label: str):
        self.dataset_iterator = iter(frame_list)
        self.feature_iterator = iter(features)
        self.dataframe_list = frame_list
        self.features = features
        self.target_label = target_label
        self.y_axis_label = {"value": target_label}

#TODO: crear un componente que gestiones los directorios y los ficheros de descarga
#TODO: crear un componente que se ocupe de descargas las imagenes del VisualizerInterface
class VisualizerInterface(VisualizerDarkSet):
    current_content = None
    title = "GRAFICO: {} respecto a {}"

    def _get_content(self):
        return next(self.dataset_iterator, None)

    def set_content(self, feature:str = None, ascending:bool = False, suffix: str = None) -> pd.DataFrame:
        if feature is None:
            self.current_content = self._get_content()
            self.current_feature = next(self.feature_iterator, None)

        else:
            for i, label in enumerate(self.features):
                if label == feature:
                    self.current_content = self.dataframe_list[i]
                    self.current_feature = feature
                    break
        
        self.current_content = self.current_content.reindex(dict(zip(self.current_content.sum().sort_values(ascending=ascending).index, self.current_content.columns)), axis=1)
        self.title_format = self.title.format(self.target_label, self.current_feature)
        if suffix is not None:
            self.title_format += f" - ({suffix})"
        return self

    def plot(self):
        self.figure = self.current_content.plot(title=self.title_format, height=self.height, width=self.width, labels=self.y_axis_label, template=self.template)
        self.figure.show()

    def plot_areas(self):
        self.figure = self.current_content.plot.area(title=self.title_format, height=self.height, width=self.width, labels=self.y_axis_label, template=self.template)
        self.figure.show()
    
    def plot_bar(self):
            self.figure = self.current_content.plot(kind="bar", title=self.title_format, height=self.height, width=self.width, labels=self.y_axis_label, template=self.template)
            self.figure.show()

# VisualizerInterface(frame_list=d3.accumulated, features=features, target_label="Ventas [USD]")
# VisualizerInterface(frame_list=d3.accumulated, features=features, target_label="Ventas [USD]").get_content()
e = VisualizerInterface(frame_list=d3.accumulated, features=features, target_label="Ventas [USD]")
e.set_content(suffix="ACUMULADO").plot_areas()
e.set_content()#.plot()

In [52]:
class VisualizerData:
    """VisualizerData: 
    - Storage some default values for graphs attributes
    - Storage a list of DataFrames
    - Storage a list with strings, must have same length than the previous list
    - Build an iterator for dataframe list
    - Build an iterator for feature list
    """
    height = 700
    width = 1200
    template = 'plotly_dark'

    def __init__(self, frame_list: list[pd.DataFrame], features: list[str]):
        self.dataset_iterator = iter(frame_list)
        self.feature_iterator = iter(features)
        self.dataframe_list = frame_list
        self.features = features
        self.figures = {}



class VisualProcessor(VisualizerData):
    current_content = None
    title="{} , {}"

    def _get_content(self):
        return next(self.dataset_iterator, None)

    def set_title(self, new_title):
        self.title_format = new_title
        return self


    def set_content(self, feature=None, y_label=None , ascending= False, title_suffix = None):
        """set_content
        Es un método que devuelve un objeto listo para aplicarsele el método "plot()".
        Si feature es None ejecuta el iterador
        Si feature corresponde a alguna feature, si existe, devuelve el dataframe correspondiente procesado
        """
        # Collect Dataframe from list by label search
        if feature is not None and self.features.count(feature) > 0:
            for i, label in enumerate(self.features):
                if label == feature:
                    self.current_content = self.dataframe_list[i]
                    self.current_feature = feature
                    break
        # Collect DataFrame from list by iterator
        else:
            if feature is not None:
                print ("logg. No se encontró la feature solicitada")
            self.current_content = self._get_content()
            self.current_feature = next(self.feature_iterator, None)
        # Ordering columns
        self.current_content = self.current_content.reindex(dict(zip(self.current_content.sum().sort_values(ascending=ascending).index, self.current_content.columns)), axis=1)
        # Set graphs attributes for plot        
        if y_label is not None:
            self.y_axis_label = {"value": y_label}
            self.title_format = self.title.format(self.current_feature, y_label)
        else:
            self.y_axis_label = {"value": "value"}
            self.title_format = self.title.format(self.current_feature, "")
        if title_suffix is not None:
            self.title_format += f" - ({title_suffix})"
        return self


    def plot(self):
        self.figure = self.current_content.plot(title=self.title_format, height=self.height, width=self.width, labels=self.y_axis_label, template=self.template)
        self.figure.show()
        if name := input("Ingrese nombre para guardar\nEnter para salir"):
            self.figures[name] = self.figure


    def plot_area(self):
        self.figure = self.current_content.plot.area(title=self.title_format, height=self.height, width=self.width, labels=self.y_axis_label, template=self.template)
        self.figure.show()
        if name := input("Ingrese nombre para guardar\nEnter para salir"):
            self.figures[name] = self.figure
    
    def plot_kind(self, kind='bar', resample=None):
        if resample is not None:
            self.figure = self.current_content.resample(resample).sum().plot(kind=kind, title=self.title_format, height=self.height, width=self.width, labels=self.y_axis_label, template=self.template)
        else:
            self.figure = self.current_content.plot(kind=kind, title=self.title_format, height=self.height, width=self.width, labels=self.y_axis_label, template=self.template)
        self.figure.show()
        if name := input("Ingrese nombre para guardar\nEnter para salir"):
            self.figures[name] = self.figure

In [54]:
vars(d1)

ft_1 = ["accum_Ventas_USD", "Cantidad"]
dataframe_list_1 = [d1.targets[[ft_1[0]]], d2.targets[[ft_1[1]]]]


visual_1 = VisualizerInterface(frame_list=dataframe_list_1, features=ft_1, target_label='correjir')
dir(VisualizerInterface)
vars(VisualizerInterface)
# help(VisualizerInterface)


visual_2 = VisualProcessor(frame_list=dataframe_list_1, features=ft_1)
visual_2.set_content(y_label="Ventas [USD]").set_title("Ventas acumuladas en USD - Período 2016-2020").plot()
visual_2.set_content(y_label="Ventas [UN.]").plot_kind(kind="bar", resample='M')

In [57]:
visual_2.figures.keys()

dict_keys(['ventas_1', '1_lineas', '2_barras'])

In [49]:
visual_3 = VisualProcessor(frame_list=d3.accumulated, features=features)

features

visual_3.set_content(feature='Sede', title_suffix="Prueba").plot()

In [26]:
"""PLOTLY TEMPLATES:https://plotly.com/python/templates/

 ['ggplot2', 'seaborn', 'simple_white', 'plotly',
         'plotly_white', 'plotly_dark', 'presentation', 'xgridoff',
         'ygridoff', 'gridon', 'none']
""";





# VISUALIZACION: STACKED AREAS
# f = contenido.plot.area(title=f'VISUALIZACION: Ventas por {next(features_iter) (Apiladas)}', height=700, width=1200, labels={'value':'Ventas'}, template='plotly_dark')
# f.show()

"""
'add_barpolar', 'add_box', 'add_candlestick', 'add_carpet', 'add_choropleth', 'add_choroplethmapbox', 'add_cone', 'add_contour', 'add_contourcarpet', 'add_densitymapbox', 'add_funnel', 'add_funnelarea', 'add_heatmap', 'add_heatmapgl', 'add_histogram', 'add_histogram2d', 'add_histogram2dcontour', 'add_hline', 'add_hrect', 'add_icicle', 'add_image', 'add_indicator', 'add_isosurface', 'add_layout_image', 'add_mesh3d', 'add_ohlc', 'add_parcats', 'add_parcoords', 'add_pie', 'add_pointcloud', 'add_sankey', 'add_scatter', 'add_scatter3d', 'add_scattercarpet', 'add_scattergeo', 'add_scattergl', 'add_scattermapbox', 'add_scatterpolar', 'add_scatterpolargl', 'add_scattersmith', 'add_scatterternary', 'add_selection', 'add_shape', 'add_splom', 'add_streamtube', 'add_sunburst', 'add_surface', 'add_table', 'add_trace', 'add_traces', 'add_treemap', 'add_violin', 'add_vline', 'add_volume', 'add_vrect', 'add_waterfall', 'append_trace', 'batch_animate', 'batch_update', 'data', 'for_each_annotation', 'for_each_coloraxis', 'for_each_geo', 'for_each_layout_image', 'for_each_mapbox', 'for_each_polar', 'for_each_scene', 'for_each_selection', 'for_each_shape', 'for_each_smith', 'for_each_ternary', 'for_each_trace', 'for_each_xaxis', 'for_each_yaxis', 'frames', 'full_figure_for_development', 'get_subplot', 'layout', 'plotly_relayout', 'plotly_restyle', 'plotly_update', 'pop', 'print_grid', 'select_annotations', 'select_coloraxes', 'select_geos', 'select_layout_images', 'select_mapboxes', 'select_polars', 'select_scenes', 'select_selections', 'select_shapes', 'select_smiths', 'select_ternaries', 'select_traces', 'select_xaxes', 'select_yaxes', 'set_subplots', 'show', 'to_dict', 'to_html', 'to_image', 'to_json', 'to_ordered_dict', 'to_plotly_json', 'update', 'update_annotations', 'update_coloraxes', 'update_geos', 'update_layout', 'update_layout_images', 'update_mapboxes', 'update_polars', 'update_scenes', 'update_selections', 'update_shapes', 'update_smiths', 'update_ternaries', 'update_traces', 'update_xaxes', 'update_yaxes', 'write_html', 'write_image', 'write_json'
""";

In [27]:
import sys

sys.exit(0)


"""

Este es un mensaje importante:

No tengo un lugar fijo para decantar mis pensamientos:

Recien aplicando data.sample() pude ver que el servicio de REENCAUCHE realizó una venta de 0.15 centavos de dolar, insignificante, y que el servicio SERVICIOS una de 2.9usd tmb es poco.

Estas observaciones no pueden quedar olvidadas

2.
Hay muchos Familias, Descripcion que solo se han vendido 1 sola vez

3. x (!) WRONG
el top 50 de los peores SERVICIOS son REENCAUCHES MAL INGRESADOS

4.
los FILTROS, top top top no reportaron más de 4000 dolares de ganancias en todo el periodo.

5.
las LLANTAS reportan ganancias inmensas, al mismo tiempo que otras reportan poco.
"""

SystemExit: 0

# (V) EXTRAS:

## 2do- PREPARAR DATASETS PARA MUESTREOS TEMPORALES

    2.1- Completar fechas faltante

    2.2- Armar muestreos temporales

    2.3- Visualizar poblacion



**EXPLICACION DEL GRAFICO**<br />
La variable "lista_mensual", es una lista cuyos elementos son datasets. <br />
Son 59 datasets que representan 1790 días en total<br />
Cada dataset representa un período de 30 días. <br />
Cada columna del gráfico representa el "len()" de un dataset. <br />
Algunos períodos tuvieron más cantidad de transacciones que otros. <br />

------DESC------

Primero tenemos que armar cada una de las series temporales

Para poder aplicar Cross-Validation a la serie temporal, es necesario completar con las fechas faltantes con algun valor default en sus variables. De esta forma podremos garantizar que nuestro folds representan el mismo timedelta.

------EJ------

Para hacer cross validation con scikit learn sobre data:

Si empezamos por 2016-01-09 y terminamos en 2020-12-02, tenemos 1790 días. Nuestro "log" es 1 día.

Como querémos cortes de igual tamaño, y sin gap al max_train_size y al test_size le damos el mismo valor.

Si quisieramos cortes bimensuales ingresamos los parámetros con valor 60 (días).

Para n_splits hacemos 1790 / 60 = 29.8 por eso elegimos 29 folds.

In [ ]:
from paquete_proyecto.preprocesamiento.muestreo import complete_dates, timeseries_cv

data_complete = complete_dates(data)

lista_mensual = timeseries_cv(data_complete, 59, 30, 30)


# VISUALIZACION:
# POBLACION: LONGITUD DE LOS DATASETS MUESTREADOS
longitud = []
for elemento in lista_mensual:
    longitud.append(len(elemento.dropna()))

pd.Series(longitud).plot.bar(figsize=(15, 5)).set(
    title="Cantidad de ventas cada 30 días"
)

In [ ]:
# TOP 50 DE LAS FAMILIAS DESCRIPCION MAS VENDIDAS
# CHEQUEAR EL TEMA DE LOS MULTIINDEX LOCO FLACO MACHO CAMPEON DE ARENA SABIO DE MONTAÑA FACHA DE LA EPOCA EJEMPLO DE MARTIR CADAVER DE LUZ
data.groupby(["Familia", "Descripcion"])["Cantidad"].count().to_frame().sort_values(
    by="Familia"
).sort_values(by="Cantidad", ascending=False).head(50)


data.groupby("Familia")["Cantidad"].count()
data.loc[data.Familia == "REENCAUCHE"].groupby(["Familia", "Descripcion"])[
    "Ventas_USD"
].count().to_frame().sort_values(by="Familia").sort_values(
    by="Ventas_USD", ascending=False
)
data.loc[data.Familia == "SERVICIOS"].groupby(["Familia", "Descripcion"])[
    "Ventas_USD"
].sum().to_frame().sort_values(by="Ventas_USD", ascending=False)

In [ ]:
"""
Familia - SERVICIOS

ES CAMION? SI O NO?

"""

In [ ]:
# crear una pivot table. que en el indice tenga fechas, en las columnas tenga localidad, y que los valores sean la cantidad de clientes que tuvo.

pd.pivot_table(
    data_complete,
    values="IdCliente",
    index="Fecha",
    columns="Localidad",
    aggfunc="count",
)